In [1]:
# Import files
import neonutilities
import os
# import pandas as pd
# import glob

# set product for field data for NEON sites
vegprod = "DP1.10098.001"

siteid = "TEAK"
url_list = neonutilities.api.list_available_urls("DP1.10098.001",siteid)
# print (url_list)  

# sets download path for NEON product

dirname = os.getcwd()
# vegdir = os.path.join(dirname, "NEON_struct-plant")
vegdir = os.path.join(dirname, "data")
if not os.path.exists(vegdir):
    os.makedirs(vegdir)
# print(vegdir)

# downloads product to set path

neonutilities.api.download_urls(url_list,download_folder_root=f"{vegdir}/", zip=False)

In [9]:
vegprod2 = "DP1.30003.001"

siteid2 = "HEAL"

url_list2 = neonutilities.api.list_available_urls(vegprod2,siteid2)

for url in url_list2:
    print(url)

https://data.neonscience.org/api/v0/data/DP1.30003.001/HEAL/2017-07
https://data.neonscience.org/api/v0/data/DP1.30003.001/HEAL/2018-08
https://data.neonscience.org/api/v0/data/DP1.30003.001/HEAL/2019-08
https://data.neonscience.org/api/v0/data/DP1.30003.001/HEAL/2021-07
https://data.neonscience.org/api/v0/data/DP1.30003.001/HEAL/2023-08


In [2]:
from glob import glob
import pandas as pd

app_indv_filenames = glob('C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_struct-plant/**/*vst_apparentindividual*.csv', recursive=True)
plot_loc_filenames = glob('C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_struct-plant/**/*vst_perplotperyear*.csv', recursive=True)
map_tag_filenames = glob('C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_struct-plant/**/*vst_mappingandtagging*.csv', recursive=True)

dfs = []

for filename in app_indv_filenames:
    month = pd.read_csv(filename)
    dfs.append(month)

    # print(filename)

all_data = pd.concat(dfs, ignore_index=False)
all_data.drop_duplicates(inplace=True)

pd.set_option('display.expand_frame_repr', False)
with pd.option_context('display.max_rows', None, 'display.max_columns', None):  # more options can be specified also
    print(all_data)

# print(len(all_data.index))

all_data.to_csv("C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_struct-plant/TEAK_appindv_allyears_2022.csv")
dfs.clear()

for filename in plot_loc_filenames:
    month = pd.read_csv(filename)
    dfs.append(month)

    # print(filename)

all_data = pd.concat(dfs, ignore_index=False)
all_data.drop_duplicates(inplace=True)

# print (all_data['plotID'])

# all_data = all_data.sort_values(by=['plotID'])
all_data.sort_values(by=['plotID'], inplace=True)

# print (all_data['plotID'])
# print(len(all_data.index))

all_data.to_csv("C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_struct-plant/TEAK_plotloc_allyears_2022.csv")
dfs.clear()

for filename in map_tag_filenames:
    month = pd.read_csv(filename)

    # get most recent mapping and tagging file
    dfs.clear()
    dfs.append(month)

all_data = pd.concat(dfs, ignore_index=False)
all_data.drop_duplicates(inplace=True)

all_data.to_csv("C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_struct-plant/TEAK_maptag_allyears_2022.csv")

# # print(len(all_data.index))

                                       uid          namedLocation        date        eventID domainID siteID    plotID            subplotID              individualID  tempStemID tagStatus        growthForm               plantStatus  stemDiameter  measurementHeight changedMeasurementLocation  height  baseCrownHeight  breakHeight  breakDiameter  maxCrownDiameter  ninetyCrownDiameter    canopyPosition                shape  basalStemDiameter  basalStemDiameterMsrmntHeight  maxBaseCrownDiameter  ninetyBaseCrownDiameter dendrometerInstallationDate initialGapMeasurementDate  initialBandStemDiameter  initialDendrometerGap  dendrometerHeight  dendrometerGap dendrometerCondition  bandStemDiameter                                            remarks               recordedBy             measuredBy                     dataEntryRecordID                     dataQF
0     2b16862c-abd8-40ad-9a5d-0226bbb78499  TEAK_045.basePlot.vst  2015-08-13  vst_TEAK_2015      D17   TEAK  TEAK_045               39_400 

In [3]:
import pandas as pd
import numpy as np
import re
import requests
import json

tree_list = []
map_tag_df = pd.read_csv("C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_struct-plant/TEAK_maptag_allyears_2022.csv")
neon_url = 'http://data.neonscience.org/api/v0/locations/'

# Set the url_loc using the namedLocation and pointID
map_tag_df.loc[np.isnan(map_tag_df['pointID']), "pointID"] = 999
map_tag_df['pointID'] = map_tag_df['pointID'].astype(int)
map_tag_df['pointID'] = map_tag_df['pointID'].astype(str)
# map_tag_df.loc[map_tag_df['pointID']=="999", "pointID"] = ""

# Create id by combining plotID and pointID and joining with plotdf
map_tag_df ['plotptid'] = map_tag_df['namedLocation'] + "." + map_tag_df["pointID"]

for plotptid in map_tag_df ['plotptid']:
    # print(plotptid)
    if not re.search('999', plotptid):
        location_url = neon_url + plotptid
        print(location_url)
        
        site_request = requests.get(location_url)
        site_json = site_request.json()

        pretty_json = json.dumps(site_json, indent=4)
        print(pretty_json)
        tree_list.append(pretty_json)


# site_request = requests.get(neon_url + site)
# site_json = site_request.json()
# plot_url = []
# tree_url = []

# # site_json['data'].keys()

# for child_url in site_json['data']['locationChildrenUrls']:
#     if re.search('.vst*', child_url):
#         plot_url.append(child_url)

# # print ('\n'.join(plot_url) + '\n')
# pretty_json = json.dumps(site_json, indent=4)
# print(pretty_json)

http://data.neonscience.org/api/v0/locations/TEAK_045.basePlot.vst.49
{
    "data": {
        "locationName": "TEAK_045.basePlot.vst.49",
        "locationDescription": "49",
        "locationType": "Point",
        "domainCode": "D17",
        "siteCode": "TEAK",
        "locationDecimalLatitude": 36.998017,
        "locationDecimalLongitude": -119.003917,
        "locationElevation": 2139.94,
        "locationUtmEasting": 321684.59895,
        "locationUtmNorthing": 4096529.37418,
        "locationUtmHemisphere": "N",
        "locationUtmZone": 11,
        "alphaOrientation": 0.0,
        "betaOrientation": 0.0,
        "gammaOrientation": 0.0,
        "xOffset": 0.0,
        "yOffset": 0.0,
        "zOffset": 0.0,
        "offsetLocation": null,
        "activePeriods": [
            {
                "activatedDate": null,
                "deactivatedDate": null
            }
        ],
        "locationProperties": [
            {
                "locationPropertyName": "Value for

In [4]:
import neonutilities

siteName = "TEAK"

url_list = neonutilities.api.list_available_urls("DP1.10098.001",siteName)
url_list

['https://data.neonscience.org/api/v0/data/DP1.10098.001/TEAK/2015-08',
 'https://data.neonscience.org/api/v0/data/DP1.10098.001/TEAK/2015-09',
 'https://data.neonscience.org/api/v0/data/DP1.10098.001/TEAK/2015-10',
 'https://data.neonscience.org/api/v0/data/DP1.10098.001/TEAK/2021-09',
 'https://data.neonscience.org/api/v0/data/DP1.10098.001/TEAK/2021-11',
 'https://data.neonscience.org/api/v0/data/DP1.10098.001/TEAK/2021-12',
 'https://data.neonscience.org/api/v0/data/DP1.10098.001/TEAK/2022-06',
 'https://data.neonscience.org/api/v0/data/DP1.10098.001/TEAK/2022-07',
 'https://data.neonscience.org/api/v0/data/DP1.10098.001/TEAK/2022-08',
 'https://data.neonscience.org/api/v0/data/DP1.10098.001/TEAK/2022-09']

In [5]:
# get utm easting and northing
import time
import requests

NEON_TOKEN = "eyJhdWQiOiJodHRwczovL2RhdGEubmVvbnNjaWVuY2Uub3JnL2FwaS92MC8iLCJzdWIiOiJhLnJvamFzODkwN0BnbWFpbC5jb20iLCJzY29wZSI6InJhdGU6cHVibGljIiwiaXNzIjoiaHR0cHM6Ly9kYXRhLm5lb25zY2llbmNlLm9yZy8iLCJleHAiOjE3OTQ3NjU0MjIsImlhdCI6MTYzNzA4NTQyMiwiZW1haWwiOiJhLnJvamFzODkwN0BnbWFpbC5jb20ifQ"
def download_tree_loc(url_list, fn):
    with open(fn, 'w') as f:
        f.write("loc_name,utmEasting,utmNorthing,utmZone,elev,coord_uncertainty,elev_uncertainty\n")
        for url in url_list:
            print(url)
            # request from url
            r =  requests.get("https://data.neonscience.org/api/v0/locations/" + url,
                              headers={'Authorization': "token " + NEON_TOKEN})
            # Get data
            loc_name = r.json()['data']['locationName']
            utmEasting = r.json()['data']['locationUtmEasting']
            utmNorthing = r.json()['data']['locationUtmNorthing']
            utmZone = r.json()['data']['locationUtmZone']
            elev = r.json()['data']['locationElevation']
            uncertainty_list = r.json()['data']['locationProperties']
            coord_uncertainty = uncertainty_list[1]['locationPropertyValue']
            elev_uncertainty = uncertainty_list[2]['locationPropertyValue']

            # write line to file
            f.write(f"{loc_name},{utmEasting},{utmNorthing},{utmZone},{elev},{coord_uncertainty},{elev_uncertainty}\n")

In [1]:
def get_date_subfolder():
    current_date = datetime.now()
    return current_date.strftime('%Y_%m_%d')

output_save_path = 'C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/'

{
    "data": {
        "locationName": "TEAK_018.basePlot.vst",
        "locationDescription": "Plot \"TEAK_018\" at site \"TEAK\"",
        "locationType": "OS Plot - vst",
        "domainCode": "D17",
        "siteCode": "TEAK",
        "locationDecimalLatitude": 36.978607,
        "locationDecimalLongitude": -119.028942,
        "locationElevation": 2307.84,
        "locationUtmEasting": 319411.62872,
        "locationUtmNorthing": 4094422.97445,
        "locationUtmHemisphere": "N",
        "locationUtmZone": 11,
        "alphaOrientation": 0.0,
        "betaOrientation": 0.0,
        "gammaOrientation": 0.0,
        "xOffset": 0.0,
        "yOffset": 0.0,
        "zOffset": 0.0,
        "offsetLocation": null,
        "activePeriods": [
            {
                "activatedDate": null,
                "deactivatedDate": null
            }
        ],
        "locationProperties": [
            {
                "locationPropertyName": "Value for Coordinate source",
            

In [7]:
pd.set_option('display.float_format', lambda x: '%.6f' % x)
plot_data_df.rename(columns ={0: 'Value for Plot dimensions', 1: 'Value for Plot ID', 2: 'Value for Plot size', 3: 'locationDecimalLatitude', 4: 'locationDecimalLongitude', 5: 'locationUtmEasting', 6: 'locationUtmNorthing'}, inplace=True)

pd.set_option('display.expand_frame_repr', False)
with pd.option_context('display.max_rows', None, 'display.max_columns', None):  # more options can be specified also
    print(plot_data_df)

plot_data_df.to_csv("C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK_LAI/TEAK_plot_data.csv")

   Value for Plot dimensions Value for Plot ID  Value for Plot size  locationDecimalLatitude  locationDecimalLongitude  locationUtmEasting  locationUtmNorthing
0                  40m x 40m          TEAK_018          1600.000000                36.978607               -119.028942       319411.628720       4094422.974450
1                  40m x 40m          TEAK_008          1600.000000                36.986255               -119.007524       321336.074830       4095231.121120
2                  40m x 40m          TEAK_045          1600.000000                36.997917               -119.003820       321692.997710       4096518.097220
3                  40m x 40m          TEAK_061          1600.000000                37.001477               -119.001573       321901.273910       4096908.878610
4                  40m x 40m          TEAK_059          1600.000000                37.001454               -119.004259       321662.194460       4096911.357560
5                  40m x 40m          TE

In [8]:
# import os
import requests
import json
# import itertools
import re
import csv

neon_url = 'https://data.neonscience.org/api/v0/locations/'
site = 'TEAK/'

site_request = requests.get(neon_url + site)
site_json = site_request.json()
plot_url = []
tree_url = []

# site_json['data'].keys()

for child_url in site_json['data']['locationChildrenUrls']:
    if re.search('.vst*', child_url):
        plot_url.append(child_url)

# print ('\n'.join(plot_url) + '\n')

for child_url in plot_url:
    site_request = requests.get(child_url)
    site_json = site_request.json()

    pretty_json = json.dumps(site_json, indent=4)
    print(pretty_json)

    for tree in site_json['data']['locationChildrenUrls']:
        remove_linebreak = tree.replace('\n', '')
        tree_url.append(remove_linebreak)

with open('teak_plot_loc.csv', 'w') as f:
    write = csv.writer(f, quoting = csv.QUOTE_ALL)
    write.writerow(tree_url)
    # for i in tree_url:
    #     write.writerow([i])

# print ('\n'.join(tree_url))

# site_request = requests.get(tree_url[0])
# site_json = site_request.json()
    
# pretty_json = json.dumps(site_json, indent=4)
# print(pretty_json)

{
    "data": {
        "locationName": "TEAK_018.basePlot.vst",
        "locationDescription": "Plot \"TEAK_018\" at site \"TEAK\"",
        "locationType": "OS Plot - vst",
        "domainCode": "D17",
        "siteCode": "TEAK",
        "locationDecimalLatitude": 36.978607,
        "locationDecimalLongitude": -119.028942,
        "locationElevation": 2307.84,
        "locationUtmEasting": 319411.62872,
        "locationUtmNorthing": 4094422.97445,
        "locationUtmHemisphere": "N",
        "locationUtmZone": 11,
        "alphaOrientation": 0.0,
        "betaOrientation": 0.0,
        "gammaOrientation": 0.0,
        "xOffset": 0.0,
        "yOffset": 0.0,
        "zOffset": 0.0,
        "offsetLocation": null,
        "activePeriods": [
            {
                "activatedDate": null,
                "deactivatedDate": null
            }
        ],
        "locationProperties": [
            {
                "locationPropertyName": "Value for Coordinate source",
            

In [9]:
# request_string = "https://data.neonscience.org/api/v0/locations/TEAK?locationType=TOWER"
request_string = "https://data.neonscience.org/api/v0/locations/TEAK?hierarchy=TRUE"
site_request = requests.get(request_string)
site_json = site_request.json()

In [10]:
import csv
import requests
import json
import pandas as pd
import numpy as np

with open('teak_plot_loc.csv', 'r') as csvfile:
    reader = csv.reader(csvfile, delimiter=',', quoting = csv.QUOTE_ALL)
    first_row = next(reader)

i = 0

# for url in first_row:
#     print (url)

#     if (i < 10):
#         site_request = requests.get(url)
#         site_json = site_request.json()

#         # print(site_json['data']['locationName'])
#         # print(site_json['data']['locationUtmEasting'])
#         # print(site_json['data']['locationUtmNorthing'])
#         pretty_json = json.dumps(site_json, indent=4)
#         print(pretty_json)
    
#     i += 1

subplot_locations_df = pd.DataFrame()
subplot_locations_df[['locationName','easting', 'northing', 'locationDecimalLatitude', 'locationDecimalLongitude']] = np.NaN

for url in first_row:
    site_request = requests.get(url)
    site_json = site_request.json()

    subplot_locations_df.at[i, 'locationName'] = site_json['data']['locationName'] 
    subplot_locations_df.at[i, 'easting'] = site_json['data']['locationUtmEasting'] 
    subplot_locations_df.at[i, 'northing'] = site_json['data']['locationUtmNorthing']
    subplot_locations_df.at[i, 'locationDecimalLatitude'] = site_json['data']['locationDecimalLatitude']
    subplot_locations_df.at[i, 'locationDecimalLongitude'] = site_json['data']['locationDecimalLongitude']

    i += 1

subplot_locations_df.to_csv('C:/Users/allen/OneDrive/Desktop/Work/data/Tree Segmentation/TEAK/NEON_struct-plant/TEAK_subplotloc_allyears_2022.csv', index = False)

C:\Users\allen\AppData\Local\Temp\ipykernel_17148\570463729.py:35: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value 'TEAK_018.basePlot.vst.51' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  subplot_locations_df.at[i, 'locationName'] = site_json['data']['locationName']


In [11]:
print(len(first_row))

for row in first_row:
    print(row)
# print(first_row)

391
https://data.neonscience.org/api/v0/locations/TEAK_018.basePlot.vst.51
https://data.neonscience.org/api/v0/locations/TEAK_018.basePlot.vst.31
https://data.neonscience.org/api/v0/locations/TEAK_018.basePlot.vst.33
https://data.neonscience.org/api/v0/locations/TEAK_018.basePlot.vst.25
https://data.neonscience.org/api/v0/locations/TEAK_018.basePlot.vst.57
https://data.neonscience.org/api/v0/locations/TEAK_018.basePlot.vst.49
https://data.neonscience.org/api/v0/locations/TEAK_018.basePlot.vst.21
https://data.neonscience.org/api/v0/locations/TEAK_018.basePlot.vst.61
https://data.neonscience.org/api/v0/locations/TEAK_018.basePlot.vst.41
https://data.neonscience.org/api/v0/locations/TEAK_045.basePlot.vst.61
https://data.neonscience.org/api/v0/locations/TEAK_045.basePlot.vst.51
https://data.neonscience.org/api/v0/locations/TEAK_045.basePlot.vst.57
https://data.neonscience.org/api/v0/locations/TEAK_045.basePlot.vst.59
https://data.neonscience.org/api/v0/locations/TEAK_045.basePlot.vst.21
ht

In [18]:
from datetime import datetime
import os

def get_date_subfolder():
    current_date = datetime.now()
    return current_date.strftime('%Y_%m_%d')

output_save_path = 'C:/Users/allen/OneDrive/Desktop/Work/Scripts/Tree Segmentation/output/'
neon_url = 'https://data.neonscience.org/api/v0/locations/'

date_subfolder = get_date_subfolder()

app_indv_100_df = pd.read_csv(os.path.join(output_save_path, date_subfolder, "TEAK_entries_perplot_full_100.csv"))
app_indv_400_df = pd.read_csv(os.path.join(output_save_path, date_subfolder, "TEAK_entries_perplot_full_400.csv"))

# Concatenate two DataFrames vertically
combined_df = pd.concat([app_indv_100_df, app_indv_400_df], axis=0)

# Get only the unique plotptids
plotptids = combined_df['plotptid'].unique().tolist()

# Filter out values that end with '.999'
plotptids_filtered = [ptid for ptid in plotptids if not str(ptid).endswith('.999')]

plotptids_filtered

for plotptid in plotptids_filtered:
    request_url = neon_url + plotptid
    print(request_url)
    location = requests.get(request_url)
    site_json = site_request.json()

https://data.neonscience.org/api/v0/locations/TEAK_011.basePlot.vst.33
https://data.neonscience.org/api/v0/locations/TEAK_011.basePlot.vst.31
https://data.neonscience.org/api/v0/locations/TEAK_011.basePlot.vst.51
https://data.neonscience.org/api/v0/locations/TEAK_025.basePlot.vst.51
https://data.neonscience.org/api/v0/locations/TEAK_025.basePlot.vst.41
https://data.neonscience.org/api/v0/locations/TEAK_005.basePlot.vst.51
https://data.neonscience.org/api/v0/locations/TEAK_005.basePlot.vst.41
https://data.neonscience.org/api/v0/locations/TEAK_005.basePlot.vst.31
https://data.neonscience.org/api/v0/locations/TEAK_006.basePlot.vst.33
https://data.neonscience.org/api/v0/locations/TEAK_006.basePlot.vst.31
https://data.neonscience.org/api/v0/locations/TEAK_006.basePlot.vst.49
https://data.neonscience.org/api/v0/locations/TEAK_006.basePlot.vst.51
https://data.neonscience.org/api/v0/locations/TEAK_011.basePlot.vst.49
https://data.neonscience.org/api/v0/locations/TEAK_001.basePlot.vst.41
https: